In [1]:
import pandas as pd
import numpy as np
import tensorflow as tf
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical
from sklearn.metrics import classification_report

In [2]:
def load_data(file_path):
    with open(file_path, 'r', encoding='utf-8') as file:
        lines = file.readlines()
    sentences = [line.strip() for line in lines]
    return sentences

In [3]:
train_data = pd.read_csv('en-ner-conll-2003-master/en-ner-conll-2003/train/train.tsv/train.tsv', sep='\t', header=None, names=['label', 'sentence'], encoding='utf-8')
dev_sentences = load_data('en-ner-conll-2003-master/en-ner-conll-2003/dev-0/in.tsv')
dev_labels = load_data('en-ner-conll-2003-master/en-ner-conll-2003/dev-0/expected.tsv')
test_sentences = load_data('en-ner-conll-2003-master/en-ner-conll-2003/test-A/in.tsv')

In [4]:
def preprocess_data(sentences, labels=None):
    tokenized_sentences = [sentence.split() for sentence in sentences]
    if labels is not None:
        tokenized_labels = [label.split() for label in labels]
        return tokenized_sentences, tokenized_labels
    return tokenized_sentences

In [5]:
train_sentences, train_labels = preprocess_data(train_data['sentence'].values, train_data['label'].values)
dev_sentences, dev_labels = preprocess_data(dev_sentences, dev_labels)
test_sentences = preprocess_data(test_sentences)

In [6]:
special_tokens = ['<PAD>', '<UNK>', '<BOS>', '<EOS>']
word2idx = {w: i + len(special_tokens) for i, w in enumerate(set(word for sentence in train_sentences for word in sentence))}
for i, token in enumerate(special_tokens):
    word2idx[token] = i

idx2word = {i: w for w, i in word2idx.items()}

label2idx = {
    'O': 0,
    'B-PER': 1, 'I-PER': 2,
    'B-ORG': 3, 'I-ORG': 4,
    'B-LOC': 5, 'I-LOC': 6,
    'B-MISC': 7, 'I-MISC': 8
}
idx2label = {i: l for l, i in label2idx.items()}

In [7]:
def encode_data(sentences, labels=None):
    encoded_sentences = [[word2idx.get(word, word2idx['<UNK>']) for word in sentence] for sentence in sentences]
    if labels is not None:
        encoded_labels = [[label2idx[label] for label in label_list] for label_list in labels]
        return encoded_sentences, encoded_labels
    return encoded_sentences

In [8]:
X_train, y_train = encode_data(train_sentences, train_labels)
X_dev, y_dev = encode_data(dev_sentences, dev_labels)
X_test = encode_data(test_sentences)

In [9]:
max_len = 1000  
X_train = pad_sequences(X_train, padding='post', maxlen=max_len)
y_train = pad_sequences(y_train, padding='post', maxlen=max_len)

X_dev = pad_sequences(X_dev, padding='post', maxlen=max_len)
y_dev = pad_sequences(y_dev, padding='post', maxlen=max_len)

X_test = pad_sequences(X_test, padding='post', maxlen=max_len)

y_train = [to_categorical(i, num_classes=len(label2idx)) for i in y_train]
y_dev = [to_categorical(i, num_classes=len(label2idx)) for i in y_dev]

In [10]:
model = tf.keras.models.Sequential([
    tf.keras.layers.Embedding(input_dim=len(word2idx), output_dim=64, input_length=max_len),
    tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(units=32, return_sequences=True)),
    tf.keras.layers.TimeDistributed(tf.keras.layers.Dense(len(label2idx), activation='softmax'))
])

model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

history = model.fit(X_train, np.array(y_train), validation_data=(X_dev, np.array(y_dev)), epochs=25, batch_size=16)

y_pred = model.predict(X_dev)
y_pred = np.argmax(y_pred, axis=-1)
y_true = np.argmax(np.array(y_dev), axis=-1)

Epoch 1/25


C:\Users\Kosmitos\AppData\Local\Programs\Python\Python312\Lib\site-packages\keras\src\layers\core\embedding.py:90: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(


60/60 ━━━━━━━━━━━━━━━━━━━━ 79s 773ms/step - accuracy: 0.8902 - loss: 0.6219 - val_accuracy: 0.9606 - val_loss: 0.1716
Epoch 2/25
60/60 ━━━━━━━━━━━━━━━━━━━━ 50s 825ms/step - accuracy: 0.9656 - loss: 0.1477 - val_accuracy: 0.9606 - val_loss: 0.1553
Epoch 3/25
60/60 ━━━━━━━━━━━━━━━━━━━━ 47s 788ms/step - accuracy: 0.9650 - loss: 0.1328 - val_accuracy: 0.9607 - val_loss: 0.1352
Epoch 4/25
60/60 ━━━━━━━━━━━━━━━━━━━━ 47s 780ms/step - accuracy: 0.9646 - loss: 0.1136 - val_accuracy: 0.9648 - val_loss: 0.1134
Epoch 5/25
60/60 ━━━━━━━━━━━━━━━━━━━━ 46s 772ms/step - accuracy: 0.9705 - loss: 0.0910 - val_accuracy: 0.9716 - val_loss: 0.0963
Epoch 6/25
60/60 ━━━━━━━━━━━━━━━━━━━━ 45s 746ms/step - accuracy: 0.9776 - loss: 0.0753 - val_accuracy: 0.9761 - val_loss: 0.0827
Epoch 7/25
60/60 ━━━━━━━━━━━━━━━━━━━━ 47s 778ms/step - accuracy: 0.9837 - loss: 0.0590 - val_accuracy: 0.9804 - val_loss: 0.0707
Epoch 8/25
60/60 ━━━━━━━━━━━━━━━━━━━━ 47s 777ms/step - accuracy: 0.9880 - loss: 0.0484 - val_accuracy: 0.983

In [11]:
y_pred_tags = [[idx2label[i] for i in row] for row in y_pred]
y_true_tags = [[idx2label[i] for i in row] for row in y_true]

print(classification_report(
    [item for sublist in y_true_tags for item in sublist],
    [item for sublist in y_pred_tags for item in sublist],
    labels=list(label2idx.values())[1:], 
    target_names=[idx2label[i] for i in list(label2idx.values())[1:]]
))

C:\Users\Kosmitos\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1517: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
C:\Users\Kosmitos\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1517: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
C:\Users\Kosmitos\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1517: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(ave

              precision    recall  f1-score   support

       B-PER       0.00      0.00      0.00         0
       I-PER       0.00      0.00      0.00         0
       B-ORG       0.00      0.00      0.00         0
       I-ORG       0.00      0.00      0.00         0
       B-LOC       0.00      0.00      0.00         0
       I-LOC       0.00      0.00      0.00         0
      B-MISC       0.00      0.00      0.00         0
      I-MISC       0.00      0.00      0.00         0

   micro avg       0.00      0.00      0.00         0
   macro avg       0.00      0.00      0.00         0
weighted avg       0.00      0.00      0.00         0



C:\Users\Kosmitos\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1517: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
C:\Users\Kosmitos\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1517: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
C:\Users\Kosmitos\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1517: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(ave

In [12]:
def correct_iob_labels(predictions):
    corrected = []
    for pred in predictions:
        corrected_sentence = []
        prev_label = 'O'
        for label in pred:
            if label.startswith('I-') and (prev_label == 'O' or prev_label[2:] != label[2:]):
                corrected_sentence.append('B-' + label[2:])
            else:
                corrected_sentence.append(label)
            prev_label = corrected_sentence[-1]
        corrected.append(corrected_sentence)
    return corrected

In [13]:
y_test_pred = model.predict(X_test)
y_test_pred = np.argmax(y_test_pred, axis=-1)
y_test_pred_tags = [[idx2label[i] for i in row] for row in y_test_pred]

y_pred_tags_corrected = correct_iob_labels(y_pred_tags)
y_test_pred_tags_corrected = correct_iob_labels(y_test_pred_tags)

8/8 ━━━━━━━━━━━━━━━━━━━━ 1s 99ms/step


In [16]:
dev_predictions = [' '.join(tags) for tags in y_pred_tags_corrected]
with open('en-ner-conll-2003-master/en-ner-conll-2003/dev-0/out.tsv', 'w', encoding='utf-8') as f:
    for prediction in dev_predictions:
        f.write("%s\n" % prediction)

In [18]:
test_predictions = [' '.join(tags) for tags in y_test_pred_tags_corrected]
with open('en-ner-conll-2003-master/en-ner-conll-2003/test-A/out.tsv', 'w', encoding='utf-8') as f:
    for prediction in test_predictions:
        f.write("%s\n" % prediction)